<p style="font-weight:bold;font-size:200%">LP Token Filter</p>

- Author: Yichen Luo
- Date: 20220814

In [9]:
import pandas as pd
import requests
import time
import os
import datetime
import re
from web3 import Web3
from hexbytes import HexBytes

from IPython.core.interactiveshell import InteractiveShell
pd.set_option('max_colwidth', 100)

RD = '/home/yichen/2022_nft/02_rdata/'
WD = '/home/yichen/2022_nft/03_wdata/root/'
RES = '/home/team_defi/04_result/'
InteractiveShell.ast_node_interactivity = 'all'

# Check LP Token

## All

In [42]:
chains = ['ethereum', 'binance', 'avalanche', 'fantom', 'polygon']

for chain in chains:
    df = pd.read_csv(f'/home/yichen/2022_nft/03_wdata/processed/root_{chain}_unwrapped.csv')
    chain
    total_length = df.shape[0]
    
    dfs = df.groupby(['root'])['tokenName'].count().reset_index()
    lp = dfs.loc[dfs['tokenName'] == 2]['root'].values
    lp_length = dfs.loc[dfs['tokenName'] == 2].shape[0] * 2
    
    df[[True if i in lp else False for i in df['root']]]['tokenSymbol'].value_counts().reset_index().head(10)
    print(f'Total Length: {total_length}, LP Length: {lp_length}, LP half: {lp_length/2} ')

'ethereum'

index  tokenSymbol
0  WETH         7091
1  USDC           29
2  SINU           16
3  MINU           15
4  KINU           13
5  CINU           12
6  TINU           12
7  GINU           10
8  HINU            8
9    CC            8

Total Length: 15217, LP Length: 14252, LP half: 7126.0 


'binance'

index  tokenSymbol
0      WBNB         3332
1      BUSD          247
2      USDT           67
3      BNFT           21
4  FACEMETA           15
5     PORTO           12
6      META           11
7        MM            8
8     LAZIO            8
9    SANTOS            7

...

index  tokenSymbol
0     WFTM            8
1     FONT            3
2     USDC            2
3      ETH            2
4     FMTO            1
5      PBL            1
6     DOMO            1
7    SUPER            1
8  FANTOMY            1
9     TART            1

Total Length: 34, LP Length: 28, LP half: 14.0 


'polygon'

index  tokenSymbol
0  WMATIC           11
1    USDC            3
2    NXTT            2
3    $KMC            1
4     GEM            1
5     ZRO            1
6  Dogioh            1
7     SYC            1
8     MRC            1
9   ROGUE            1

Total Length: 45, LP Length: 28, LP half: 14.0 


## Filter: Simple Remove

### Common Bases

In [104]:
chains = [('ethereum', 'WETH'), ('binance', 'WBNB'), ('avalanche', 'WAVAX'), ('fantom', 'WFTM'), ('polygon', 'WMatic')]
bases = ['USDC', 'USDT', 'BTC', 'ETH', 'Dai', 'BUSD', 'MIM']
basesplus = bases + [i + '.e' for i in bases]

for chain in chains:
    df = pd.read_csv(f'/home/yichen/2022_nft/03_wdata/processed/root_{chain[0]}_unwrapped.csv')
    df['base'] = False
    for idx, row in df.iterrows():
        root = row['root']
        tokenSymbol = row['tokenSymbol']
        for base in basesplus:
            if base.lower() == tokenSymbol.lower():
                df.loc[(df['root'] == root)&(df['tokenSymbol'] == tokenSymbol), 'base'] = True
                print(f'{chain[0]}:{tokenSymbol} is a common base.')
        if chain[1].lower() == tokenSymbol.lower():
            df.loc[(df['root'] == root)&(df['tokenSymbol'] == tokenSymbol), 'base'] = True
            print(f'{chain[0]}:{tokenSymbol} is a common base')
            
    df.to_csv(f'/home/yichen/team_defi/04_result/insider_trading/root_list/grave/root_{chain[0]}_unwrapped.csv', index=False)

ethereum:DAI is a common base.
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:USDC is a common base.
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:USDC is a common base.
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethereum:WETH is a common base
ethere

### Automatic Check

In [105]:
chains = ['ethereum', 'binance', 'avalanche', 'fantom', 'polygon']

for chain in chains:
    chain
    df = pd.read_csv(f'/home/yichen/team_defi/04_result/insider_trading/root_list/grave/root_{chain}_unwrapped.csv')
    done = df.loc[df['base'] == True, 'tokenSymbol'].count()
    
    lp = df.loc[df['base'] == False].groupby(['root'])['tokenName'].count().reset_index()
    lp_root = lp.loc[lp['tokenName'] == 2]['root'].values
    
    todo = df[[True if i in lp_root else False for i in df['root']]]['tokenSymbol'].value_counts().reset_index()['tokenSymbol'].sum()/2
    
    print(f'{chain}, {done} / {(todo+done)}, percentage={done/(todo+done)}')

'ethereum'

ethereum, 7128 / 7129.0, percentage=0.9998597278720718


'binance'

binance, 3666 / 3682.0, percentage=0.9956545355784899


'avalanche'

avalanche, 770 / 771.0, percentage=0.9987029831387808


'fantom'

fantom, 12 / 14.0, percentage=0.8571428571428571


'polygon'

polygon, 14 / 14.0, percentage=1.0


In [106]:
chains = ['ethereum', 'binance', 'avalanche', 'fantom', 'polygon']

for chain in chains:
    df = pd.read_csv(f'/home/yichen/team_defi/04_result/insider_trading/root_list/grave/root_{chain}_unwrapped.csv')
    print(chain)
    
    df.loc[df['base'] == True, 'tokenSymbol'].value_counts()
    
    lp = df.loc[df['base'] == False].groupby(['root'])['tokenName'].count().reset_index()
    lp_root = lp.loc[lp['tokenName'] == 2]['root'].values
    
    df[[True if i in lp_root else False for i in df['root']]]['tokenSymbol'].value_counts().reset_index()
    df[[True if i in lp_root else False for i in df['root']]]

ethereum


WETH    7092
USDC      29
DAI        3
USDT       3
BTC        1
Name: tokenSymbol, dtype: int64

index  tokenSymbol
0    GUMP            1
1  PEOPLE            1

root            tokenName  \
2863  0xd509ad2af3356ce1df748cfd5bca19ad1b199f7c  The Myth of America   
2864  0xd509ad2af3356ce1df748cfd5bca19ad1b199f7c      ConstitutionDAO   

     tokenSymbol                             contractAddress   base  
2863        GUMP  0x447088Ca6F0f826C8Db4b0DAAEbfB4119BcDb368  False  
2864      PEOPLE  0x7A58c0Be72BE218B41C608b7Fe7C5bB630736C71  False

binance


...

root          tokenName tokenSymbol  \
18  0x4d49c520d6838bcf983c0b4904bc98ebc3a0762a           xRadiant        xRAY   
19  0x4d49c520d6838bcf983c0b4904bc98ebc3a0762a         Spirit LPs   SPIRIT-LP   
22  0x027cbbb914b650b065b597d9be9bbecb411c93c7  FantonMainTestTwo        FMTT   
23  0x027cbbb914b650b065b597d9be9bbecb411c93c7  FantonMainTestOne        FMTO   

                               contractAddress   base  
18  0x6e1c0af252C3f70c7BA3DA62bFf76A875814eC56  False  
19  0x6ED814F822D283d0c3632Be7B08A380742C01194  False  
22  0x2314f23778A0192A695F07A5a89181e9b7b38b66  False  
23  0x2faa34a2d23B74Dc2b32CcbA61AC6286ed98B303  False

polygon


WMATIC    11
USDC       3
Name: tokenSymbol, dtype: int64

Empty DataFrame
Columns: [index, tokenSymbol]
Index: []

Empty DataFrame
Columns: [root, tokenName, tokenSymbol, contractAddress, base]
Index: []

### Manual Check

In [283]:
chain = 'polygon'
df = pd.read_csv(f'/home/yichen/team_defi/04_result/insider_trading/root_list/grave/root_{chain}_unwrapped.csv')

In [268]:
tf = pd.read_csv(f'/home/yichen/2022_nft/03_wdata/root/tf_{chain}.csv')
tf.loc[(tf['from'] == '0xe796a7f416b568f85b7c2e166755f58af09d929a')|(tf['to'] == '0xe796a7f416b568f85b7c2e166755f58af09d929a')]

blockNumber   timeStamp  \
510      8157660  1639345173   
526      8181893  1639393874   

                                                                   hash  \
510  0x267c34b60c24845d4a92b18973f6e2c1c470c31a533a410626a82f52fcc22915   
526  0x9ae79538f216679bc2079dde3fc2d5f9e1b42eee183ad6c9bce7626398d7a4cd   

     nonce  \
510    320   
526    387   

                                                              blockHash  \
510  0x49fe19f36446251c47c6efbcb2657d6501c0150ac8cc8741d1e5ade69d508d70   
526  0x453723cbe9c27d0103d8348913136a1657fc2af36645e1d427004ed66f77161a   

                                           from  \
510  0xe796a7f416b568f85b7c2e166755f58af09d929a   
526  0xe2fe530c047f2d85298b07d9333c05737f1435fb   

                                contractAddress  \
510  0x656e74766660394ddec42920efe96b00f1a8f554   
526  0x656e74766660394ddec42920efe96b00f1a8f554   

                                             to                 value  \
510  0xe2fe530c047f2d85298b07d9333c05737f1435fb  20860027020896876250   
526  0xe796a7f416b568f85b7c2e166755f58af09d929a  20860027020896876250   

        tokenName tokenSymbol  tokenDecimal  transactionIndex     gas  \
510  Joe LP Token         JLP            18                 4  600000   
526  Joe LP Token         JLP            18                29  600000   

        gasPrice  gasUsed  cumulativeGasUsed       input  confirmations  
510  50000000000   267627            1400913  deprecated        8157390  
526  25000000000   112339            3727760  deprecated        8133157

In [279]:
df.loc[(df['root'] == '0x027cbbb914b650b065b597d9be9bbecb411c93c7')&(df['tokenSymbol'] == 'FMTO'), 'base'] = True

In [284]:
lp = df.loc[df['base'] == False].groupby(['root'])['tokenName'].count().reset_index()
lp_root = lp.loc[lp['tokenName'] == 2]['root'].values

df[[True if i in lp_root else False for i in df['root']]]

Empty DataFrame
Columns: [root, tokenName, tokenSymbol, contractAddress, base]
Index: []

In [285]:
df
df = df.loc[df['base'] == False]
df

root              tokenName  \
0   0x9b09783e11ce3b5abc4cd180cc0ca6ff366a0893  TrustSwap Token (PoS)   
1   0xca93f8e26d578d3577175bd66f521a129e9b7c61                   $KMC   
2   0xb4738b703df076b947c41936daaf69764f900b75             CUBO token   
3   0xf27195736ca77a93f5f49dd8b22148504ed211d5           BitblocksDAO   
4   0xd152f549545093347a162dce210e7293f1452150          maticroll.org   
5   0x34270b4f9aa3030950bbeca276b88ec24e1e0ccc                 Hasbik   
6   0x262e1a7e62dbb9321dcaa1f1e13a77b4da0f411d            Echelon DAO   
7   0xe4446149378eb48464f760b4817bcc35cb382a91              TrustTest   
8   0x0ce43b06128508573571da476a01cd9efad50dfb                 Hasbik   
9   0x7a78fa6faee518a45d3c3560a881dbea1cb76f92  Vault Hill City (PoS)   
10  0x93192b40486f4731dc489b29373b10e962ef76bb         Credit Cleaner   
11  0x2a669c137f50ebbe5c14219d53879115386e4e93              Zuki Moba   
12  0xa07dae8b97e81446608876eafa76c77e10196a7c            Poker Token   
13  0x264050256433fab3a38cddaa934847382f2c91b9            Poker Token   
14  0x129f027a491d96abced68cc30976797a42987303          Pleasure Coin   
15  0x61b17f09b2f90e5726b33fb74ae353a8ac04b297                Coinerr   
16  0x5ddf892d795f7d208c1d9b6119820f5df843a99f             Zombie Inu   
17  0x5ef3d7a2583baec961be19302c604c7f914138be          Wrapped Matic   
18  0x5ef3d7a2583baec961be19302c604c7f914138be                   $KMC   
19  0x5dc1139915c6a88bdb18012c6741efdf42a29f49          Wrapped Matic   
20  0x5dc1139915c6a88bdb18012c6741efdf42a29f49      NFTmall GEM Token   
21  0x5cb6a7cba0e863164111ae710e8cbd4c200c3996          Wrapped Matic   
22  0x5cb6a7cba0e863164111ae710e8cbd4c200c3996               ZROToken   
23  0x066c3607dd811a48f229f6dbfe4e73dd199830e4         USD Coin (PoS)   
24  0x066c3607dd811a48f229f6dbfe4e73dd199830e4           Dogioh Token   
25  0xcea9afdc83ac2aac6a0748f9569a49ab06acf58b          Wrapped Matic   
26  0xcea9afdc83ac2aac6a0748f9569a49ab06acf58b       Shiba Yacht Club   
27  0x59330c43dd00730b4df3326617772a0b484e3b44          Wrapped Matic   
28  0x59330c43dd00730b4df3326617772a0b484e3b44             MeroeChain   
29  0xd206f24c02cd5ea4354f1f5a33c77bbf4d3bec27          Wrapped Matic   
30  0xd206f24c02cd5ea4354f1f5a33c77bbf4d3bec27             ROGUE COIN   
31  0x24ceaecfe7d72f5064e13c3bdc436d36482c7308         USD Coin (PoS)   
32  0x24ceaecfe7d72f5064e13c3bdc436d36482c7308             OkLetsPlay   
33  0x4dbe648f797e7ec51da3eae23a89b971b4e022a5          Wrapped Matic   
34  0x4dbe648f797e7ec51da3eae23a89b971b4e022a5            Chihiro Inu   
35  0x5a6dc942826807539ca19d21c132e4b004075de0         NextEarthToken   
36  0x5a6dc942826807539ca19d21c132e4b004075de0          Wrapped Matic   
37  0x3030f09fe7ea8fa6762c13d12afa8541cb2c6644         USD Coin (PoS)   
38  0x3030f09fe7ea8fa6762c13d12afa8541cb2c6644                 Dogioh   
39  0x81411b800dcc935e1aaf0ed01dd1c0777236153c          Wrapped Matic   
40  0x81411b800dcc935e1aaf0ed01dd1c0777236153c                   POKI   
41  0xadc42c844b8392ca353e079030609b6303d7f51d          Wrapped Matic   
42  0xadc42c844b8392ca353e079030609b6303d7f51d                   Poge   
43  0x3ef7442df454ba6b7c1deec8ddf29cfb2d6e56c7         NextEarthToken   
44  0x3ef7442df454ba6b7c1deec8ddf29cfb2d6e56c7          Wrapped Matic   

      tokenSymbol                             contractAddress   base  
0            SWAP  0x3809dcdd5dde24b37abe64a5a339784c3323c44f  False  
1            $KMC  0x44d09156c7b4acf0c64459fbcced7613f5519918  False  
2            CUBO  0x381d168de3991c7413d46e3459b48a5221e3dfe4  False  
3            XBBX  0xec79b78bcedf3c4b6d12c27ba6d092ad178b5b30  False  
4   maticroll.org  0x3de2aa73ca38625ea0c6a6f36ab08c5c90c3fc5b  False  
5             HAS  0x01c4c105076bdb01ba329543ff99c85f4097a9c9  False  
6            ECHO  0x55e29f7280565d6c392c192161de9e57b125165b  False  
7            TEST  0xbfa6b51f6b09ad354f2e39a006339542f08af95a  False  
8             HAS  0x01c4c105076bdb01ba32954

root              tokenName  \
0   0x9b09783e11ce3b5abc4cd180cc0ca6ff366a0893  TrustSwap Token (PoS)   
1   0xca93f8e26d578d3577175bd66f521a129e9b7c61                   $KMC   
2   0xb4738b703df076b947c41936daaf69764f900b75             CUBO token   
3   0xf27195736ca77a93f5f49dd8b22148504ed211d5           BitblocksDAO   
4   0xd152f549545093347a162dce210e7293f1452150          maticroll.org   
5   0x34270b4f9aa3030950bbeca276b88ec24e1e0ccc                 Hasbik   
6   0x262e1a7e62dbb9321dcaa1f1e13a77b4da0f411d            Echelon DAO   
7   0xe4446149378eb48464f760b4817bcc35cb382a91              TrustTest   
8   0x0ce43b06128508573571da476a01cd9efad50dfb                 Hasbik   
9   0x7a78fa6faee518a45d3c3560a881dbea1cb76f92  Vault Hill City (PoS)   
10  0x93192b40486f4731dc489b29373b10e962ef76bb         Credit Cleaner   
11  0x2a669c137f50ebbe5c14219d53879115386e4e93              Zuki Moba   
12  0xa07dae8b97e81446608876eafa76c77e10196a7c            Poker Token   
13  0x264050256433fab3a38cddaa934847382f2c91b9            Poker Token   
14  0x129f027a491d96abced68cc30976797a42987303          Pleasure Coin   
15  0x61b17f09b2f90e5726b33fb74ae353a8ac04b297                Coinerr   
16  0x5ddf892d795f7d208c1d9b6119820f5df843a99f             Zombie Inu   
18  0x5ef3d7a2583baec961be19302c604c7f914138be                   $KMC   
20  0x5dc1139915c6a88bdb18012c6741efdf42a29f49      NFTmall GEM Token   
22  0x5cb6a7cba0e863164111ae710e8cbd4c200c3996               ZROToken   
24  0x066c3607dd811a48f229f6dbfe4e73dd199830e4           Dogioh Token   
26  0xcea9afdc83ac2aac6a0748f9569a49ab06acf58b       Shiba Yacht Club   
28  0x59330c43dd00730b4df3326617772a0b484e3b44             MeroeChain   
30  0xd206f24c02cd5ea4354f1f5a33c77bbf4d3bec27             ROGUE COIN   
32  0x24ceaecfe7d72f5064e13c3bdc436d36482c7308             OkLetsPlay   
34  0x4dbe648f797e7ec51da3eae23a89b971b4e022a5            Chihiro Inu   
35  0x5a6dc942826807539ca19d21c132e4b004075de0         NextEarthToken   
38  0x3030f09fe7ea8fa6762c13d12afa8541cb2c6644                 Dogioh   
40  0x81411b800dcc935e1aaf0ed01dd1c0777236153c                   POKI   
42  0xadc42c844b8392ca353e079030609b6303d7f51d                   Poge   
43  0x3ef7442df454ba6b7c1deec8ddf29cfb2d6e56c7         NextEarthToken   

      tokenSymbol                             contractAddress   base  
0            SWAP  0x3809dcdd5dde24b37abe64a5a339784c3323c44f  False  
1            $KMC  0x44d09156c7b4acf0c64459fbcced7613f5519918  False  
2            CUBO  0x381d168de3991c7413d46e3459b48a5221e3dfe4  False  
3            XBBX  0xec79b78bcedf3c4b6d12c27ba6d092ad178b5b30  False  
4   maticroll.org  0x3de2aa73ca38625ea0c6a6f36ab08c5c90c3fc5b  False  
5             HAS  0x01c4c105076bdb01ba329543ff99c85f4097a9c9  False  
6            ECHO  0x55e29f7280565d6c392c192161de9e57b125165b  False  
7            TEST  0xbfa6b51f6b09ad354f2e39a006339542f08af95a  False  
8             HAS  0x01c4c105076bdb01ba329543ff99c85f4097a9c9  False  
9             VHC  0x51b5619f5180e333d18b6310c8d540aea43a0371  False  
10             CC  0xe9c27e7aec171662488edd9dbc97272ec280f632  False  
11           ZUKI  0x3ec0f0f35164b433bf7e3408f797865d448935d9  False  
12           POKR  0x872361dd09900ab9f9ee3c5c80672c57d42525e7  False  
13           POKR  0x872361dd09900ab9f9ee3c5c80672c57d42525e7  False  
14           NSFW  0x8f006d1e1d9dc6c98996f50a4c810f17a47fbf19  False  
15            ERR  0xfb32513135e3267995268e3099d2b6114d20b6ed  False  
16           ZINU  0x21f9b5b2626603e3f40bfc13d01afb8c431d382f  False  
18           $KMC  0x44d09156c7b4ACf0C64459Fbcced7613F5519918  False  
20            GEM  0x4A7b9A4589A88A06ca29F99556dB08234078D727  False  
22            ZRO  0x6AcdA5E7EB1117733DC7Cb6158fc67f226b32022  False  
24         Dogioh  0x790540Ff6117205ac6eF132A5782bA4f4A611355  False  
26            SYC  0xDbb52129D1561b3AEFcaDD14D0bC02a3aC34a10D  False  
28            MRC  0xECd877434F0b7fedA377c9C5868EE42cc8F2A145  False  
3

In [286]:
df.to_csv(f'/home/yichen/team_defi/04_result/insider_trading/root_list/root_list_without_base/root_{chain}.csv', index=False)

## Filter: Contract

In [287]:
chains = ['ethereum', 'binance', 'avalanche', 'fantom', 'polygon']

for chain in chains:
    df = pd.read_csv(f'/home/yichen/team_defi/04_result/insider_trading/root_list/root_list_without_base/root_{chain}.csv')
    for idx, row in df.drop_duplicates('root').iterrows():

        root = row['root']

        if chain == 'ethereum': rpc = 'https://rpc.ankr.com/eth'
        if chain == 'binance': rpc = 'https://bscrpc.com'
        if chain == 'avalanche': rpc = 'https://api.avax.network/ext/bc/C/rpc'
        if chain == 'fantom': rpc = 'https://rpc.ftm.tools'
        if chain == 'polygon': rpc = 'https://polygon-rpc.com'

        w3 = Web3(Web3.HTTPProvider(rpc))
        contract = w3.eth.getCode(w3.toChecksumAddress(root)).hex() != '0x'
        df.loc[df['root'] == root, 'contract'] = contract
        print(f'{chain}, {root}: {contract}')

    df = df.loc[df['contract'] == False].drop(columns=['base', 'contract'])
    df.to_csv(f'/home/yichen/team_defi/04_result/insider_trading/root_list/root_list_without_base_and_contract/root_{chain}.csv', index=False)

ethereum, 0x742025b32fdda654df1aa5ae348928331ff05062: False
ethereum, 0xef0121d57d9e4324c3de83cf2a686ff5ac13c3a4: False
ethereum, 0xa625141e73ab1af1b57efbbad9ba9ab8813393e3: False
ethereum, 0x6e86c831b85cc37f0aeeb5d553c40b257af8fb42: False
ethereum, 0x72969afa049fa40e808d42f807ef4640a7cac5ec: False
ethereum, 0xf8fd86e76a0698eb02b42be5a712648ff1917331: False
ethereum, 0x154922e74d108b1f92d702529b31027de54a1933: False
ethereum, 0xa2608089b0c7321f10c1a28f9952d59781dab59b: False
ethereum, 0x24e8f3941916781a1e934426fb9d331ad2a01a5c: False
ethereum, 0xfc23ef8bc092d172e4045277570098ffa5d18fb6: False
ethereum, 0x2d74bee7ffdec1c70218c439475319d81a5cf8ec: False
ethereum, 0xfb623d04d39c4cc4b4577bd606fb14a4acab0b21: False
ethereum, 0x51a1318fc8c8822e7461a3054599b5f5efe94d5f: False
ethereum, 0xc77dd9685467194323321f229b9e2fd1692778d0: False
ethereum, 0xa4196e224a4a23a6293f55522ec11ef14037b552: False
ethereum, 0x1804b2f6467ec5d563251f1615f1964daeaa9db1: False
ethereum, 0xd95758303cb27bd8d20f0d58a382

## Filter: Burn

In [289]:
chains = ['ethereum', 'binance', 'avalanche', 'fantom', 'polygon']

for chain in chains:
    df = pd.read_csv(f'/home/yichen/team_defi/04_result/insider_trading/root_list/root_list_without_base_and_contract/root_{chain}.csv')
    df.shape[0]
    df = df.loc[df['root']!= '0x0000000000000000000000000000000000000000']
    df = df.loc[df['root']!= '0x000000000000000000000000000000000000dead']
    df.shape[0]
    df.to_csv(f'/home/yichen/team_defi/04_result/insider_trading/root_list/root_list_final/root_{chain}.csv', index=False)

8065

8064

5859

5857

841

840

17

17

29

29

# Correct Insider Transaction database

In [ ]:
import datetime
starttime = datetime.datetime.now()

df = pd.read_csv(f'{RES}/insider_trading/root/teamwallet_insider_without_contract&burn.csv')
length = df.shape[0]

chains = ['ethereum', 'binance', 'avalanche', 'fantom', 'polygon']

for idx, row in df.iterrows():
    try:
        root_info = row['insider_root']
        chain = row['chain']
        root = pd.read_csv(f'/home/yichen/team_defi/04_result/insider_trading/root_list/root_list_final/root_{chain}.csv')
        
        endtime = datetime.datetime.now()
        duration = (endtime-starttime).seconds / 60
        lefttime = (duration / (idx + 1)) * (length- idx)
        
        print(f'{idx}/{length}, {lefttime} min left')
        
        tokenName = root.loc[root['root'] == root_info, 'tokenName'].values[0]
        tokenSymbol = root.loc[root['root'] == root_info, 'tokenSymbol'].values[0]
        contractAddress = root.loc[root['root'] == root_info, 'contractAddress'].values[0]

        df.loc[df['insider_root'] == root_info, 'insider_tokenName'] = tokenName
        df.loc[df['insider_root'] == root_info, 'insider_tokenSymbol'] = tokenSymbol
        df.loc[df['insider_root'] == root_info, 'insider_contractAddress'] = contractAddress
        
    except:
        df = df.loc[(df['insider_root'] != root_info)|(df['chain'] != chain)]
        chain, root_info
    
df.to_csv(f'{RES}/insider_trading/root/teamwallet_insider_new.csv', index=False)

/tmp/ipykernel_3313255/4000410848.py:4: DtypeWarning: Columns (3,4,6) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(f'{RES}/insider_trading/root/teamwallet_insider_without_contract&burn.csv')


0/110775, 0.0 min left
1/110775, 0.0 min left
2/110775, 0.0 min left
3/110775, 0.0 min left
4/110775, 0.0 min left
5/110775, 0.0 min left
6/110775, 0.0 min left
7/110775, 0.0 min left
8/110775, 0.0 min left
9/110775, 0.0 min left
10/110775, 167.82575757575756 min left
11/110775, 153.8388888888889 min left
12/110775, 142.00384615384615 min left
13/110775, 131.8595238095238 min left
14/110775, 123.06777777777778 min left
15/110775, 115.375 min left
16/110775, 108.58725490196078 min left
17/110775, 102.5537037037037 min left
18/110775, 97.15526315789474 min left
19/110775, 92.29666666666667 min left
20/110775, 87.90079365079364 min left
21/110775, 83.90454545454546 min left
22/110775, 80.25579710144928 min left
23/110775, 76.91111111111111 min left
24/110775, 73.834 min left
25/110775, 70.99358974358974 min left
26/110775, 68.36358024691359 min left
27/110775, 65.92142857142856 min left
28/110775, 63.64770114942529 min left
29/110775, 61.525555555555556 min left
30/110775, 59.540322580645

('ethereum', '0x9124a33ea0574e894dcc31a3e7754bb8b5f01d09')

2211/110775, 53.987522603978306 min left


('ethereum', '0x9124a33ea0574e894dcc31a3e7754bb8b5f01d09')

...

38886/110775, 35.648405636845226 min left


('ethereum', '0xd509ad2af3356ce1df748cfd5bca19ad1b199f7c')

38887/110775, 35.646993074127415 min left


('ethereum', '0xd509ad2af3356ce1df748cfd5bca19ad1b199f7c')

38888/110775, 35.64558058405548 min left
38889/110775, 35.644168166623814 min left
38890/110775, 35.64275582182682 min left
38891/110775, 35.641343549658885 min left
38892/110775, 35.63993135011442 min left
38893/110775, 35.638519223187814 min left
38894/110775, 35.63710716887346 min left
38895/110775, 35.63569518716578 min left
38896/110775, 35.63428327805915 min left
38897/110775, 35.632871441547984 min left
38898/110775, 35.66225609912851 min left
38899/110775, 35.660843187660674 min left
38900/110775, 35.65943034883422 min left
38901/110775, 35.658017582643566 min left
38902/110775, 35.656604889083106 min left
38903/110775, 35.65519226814723 min left
38904/110775, 35.653779719830354 min left
38905/110775, 35.65236724412687 min left
38906/110775, 35.65095484103118 min left
38907/110775, 35.64954251053768 min left
38908/110775, 35.64813025264078 min left
38909/110775, 35.646718067334874 min left
38910/110775, 35.64530595461438 min left
38911/110775, 35.643893914473686 min left
38912/